# Testing Snowplow Algorithm

In [77]:
import os
# switch directories for import
os.chdir('c:\\Users\\Sneez\\Desktop\\Snowplowing\\Snowplow-Routing-Middleton\\Snowplow-Routing-Middleton')

import initialize
import params
from sectioning_streets import sectioning
from importlib import reload
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


Autoreload documentation: https://ipython.readthedocs.io/en/stable/config/extensions/autoreload.html

For reloading user modules

In [78]:
toyEdgeFile = "C:\\Users\\Sneez\\Desktop\\Snowplowing\\Snowplow-Routing-Middleton\\Snowplow-Routing-Middleton\\graph_data\\edges.csv"
toyNodeFile = "C:\\Users\\Sneez\\Desktop\\Snowplowing\\Snowplow-Routing-Middleton\\Snowplow-Routing-Middleton\\graph_data\\nodes.csv"

In [79]:
instance = "sectionedfullstreets"
polygon_path = "C:\\Users\\Sneez\\Desktop\\Snowplowing\\Data+Info\\GIS Data\\IndividualRoutes\\MiddletonRoute3-blue.gpkg"

match instance:
    case "smallstreets":
        G = initialize.create_small_streets()
    case "fullstreets":
        G = initialize.create_full_streets()
    case "smalltoy":
        G = initialize.create_small_toy(toyEdgeFile, toyNodeFile)
    case "sectionedfullstreets":
        G = sectioning.section_component(polygon_path)
    case _:
        print("Invalid instance name")
     

Update depot

In [80]:
params.DEPOT = params.find_depot(G)[0]
params.DEPOT

113

Now reload all other modules for updated depot

In [81]:
os.chdir('c:\\Users\\Sneez\\Desktop\\Snowplowing\\Snowplow-Routing-Middleton\\Snowplow-Routing-Middleton')

import dual_graphs
import pandas as pd
import construction
import shortest_paths
import crossover
import osmnx as ox
import genetic 
import solution 
import costs 
import plotting
import local_search
import folium
import folium.plugins
%load_ext autoreload
%autoreload 2

dual_graphs = reload(dual_graphs)
construction = reload(construction)
shortest_paths = reload(shortest_paths)
crossover = reload(crossover)
genetic = reload(genetic)
solution = reload(solution)
costs = reload(costs)
plotting = reload(plotting)
local_search = reload(local_search)

from shortest_paths import ShortestPaths
from crossover import apply_crossover
from genetic import run_genetic
from solution import Solution
from routes_representations import RouteStep
from costs import routes_cost
from params import *

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [82]:
approach = "genetic"

if approach == "genetic":
    G = initialize.add_multi_edges(G)
    if instance == "smallstreets" or instance == "fullstreets" or instance == "sectionedfullstreets":
        G_DUAL = dual_graphs.create_dual_streets(G)
    else:
        G_DUAL = dual_graphs.create_dual_toy(G)

elif approach == "annealing":
    if instance == "smallstreets" or instance == "fullstreets" or instance == "sectionedfullstreets":
        G_DUAL = dual_graphs.create_dual_streets(G, False, True)
    else:
        G_DUAL = dual_graphs.create_dual_toy(G, False, True)



In [83]:
print(G)
print(G_DUAL)

MultiDiGraph with 163 nodes and 722 edges
MultiDiGraph with 723 nodes and 3997 edges


In [84]:
sp = ShortestPaths(G_DUAL, False, True)

In [85]:
construction.process_node(G, 0, 1)

([], inf, -inf)

In [86]:
r, rreq = construction.route_generation(G, sp)


In [87]:
for route in r:
    for routestep in route:
        print(routestep)
    print("***")


113 --> 110. (0) Salt value: 20000. Prev: None. Next: (110, 112, 2). Route end: False
110 --> 112. (2) Salt value: 19987.1938543755. Prev: (113, 110, 0). Next: (112, 114, 1). Route end: False
112 --> 114. (1) Salt value: 19957.96285376525. Prev: (110, 112, 2). Next: (114, 124, 2). Route end: False
114 --> 124. (2) Salt value: 19936.887968901. Prev: (112, 114, 1). Next: (124, 125, 2). Route end: False
124 --> 125. (2) Salt value: 19915.413542483748. Prev: (114, 124, 2). Next: (125, 111, 0). Route end: False
125 --> 111. (0) Salt value: 19908.58312176625. Prev: (124, 125, 2). Next: (111, 113, 1). Route end: False
111 --> 113. (1) Salt value: 19888.9712549215. Prev: (125, 111, 0). Next: (113, 110, 1). Route end: False
***
113 --> 110. (1) Salt value: 20000. Prev: (111, 113, 1). Next: (110, 111, 1). Route end: False
110 --> 111. (1) Salt value: 19987.1938543755. Prev: (113, 110, 1). Next: (111, 113, 0). Route end: False
111 --> 113. (0) Salt value: 19985.64834935575. Prev: (110, 111, 1). N

In [88]:
for route in rreq:
    for routestep in route:
        print(routestep)
    print("**")

113 --> 110. (0) Salt value: 20000. Prev: None. Next: (110, 112, 2). Route end: False
110 --> 112. (2) Salt value: 19987.1938543755. Prev: (113, 110, 0). Next: (112, 114, 1). Route end: False
112 --> 114. (1) Salt value: 19957.96285376525. Prev: (110, 112, 2). Next: (114, 124, 2). Route end: False
114 --> 124. (2) Salt value: 19936.887968901. Prev: (112, 114, 1). Next: (124, 125, 2). Route end: False
124 --> 125. (2) Salt value: 19915.413542483748. Prev: (114, 124, 2). Next: (125, 111, 0). Route end: False
125 --> 111. (0) Salt value: 19908.58312176625. Prev: (124, 125, 2). Next: (111, 113, 1). Route end: False
111 --> 113. (1) Salt value: 19888.9712549215. Prev: (125, 111, 0). Next: (113, 110, 1). Route end: False
**
113 --> 110. (1) Salt value: 20000. Prev: (111, 113, 1). Next: (110, 111, 1). Route end: False
110 --> 111. (1) Salt value: 19987.1938543755. Prev: (113, 110, 1). Next: (111, 113, 0). Route end: False
111 --> 113. (0) Salt value: 19985.64834935575. Prev: (110, 111, 1). Ne

Test Local Search

In [89]:
required_edges = set(edge[:3] for edge in G.edges(data=True, keys=True) if edge[3]['priority'] != 0)
S_first = Solution(rreq, dict(), routes_cost(G, sp, rreq), 0)

print(routes_cost(G, sp, S_first.routes))
for route in S_first.routes:
    for routestep in route:
        print(routestep)
    print("**")

3989999.640000003
113 --> 110. (0) Salt value: 20000. Prev: None. Next: (110, 112, 2). Route end: False
110 --> 112. (2) Salt value: 19987.1938543755. Prev: (113, 110, 0). Next: (112, 114, 1). Route end: False
112 --> 114. (1) Salt value: 19957.96285376525. Prev: (110, 112, 2). Next: (114, 124, 2). Route end: False
114 --> 124. (2) Salt value: 19936.887968901. Prev: (112, 114, 1). Next: (124, 125, 2). Route end: False
124 --> 125. (2) Salt value: 19915.413542483748. Prev: (114, 124, 2). Next: (125, 111, 0). Route end: False
125 --> 111. (0) Salt value: 19908.58312176625. Prev: (124, 125, 2). Next: (111, 113, 1). Route end: False
111 --> 113. (1) Salt value: 19888.9712549215. Prev: (125, 111, 0). Next: (113, 110, 1). Route end: False
**
113 --> 110. (1) Salt value: 20000. Prev: (111, 113, 1). Next: (110, 111, 1). Route end: False
110 --> 111. (1) Salt value: 19987.1938543755. Prev: (113, 110, 1). Next: (111, 113, 0). Route end: False
111 --> 113. (0) Salt value: 19985.64834935575. Prev:

In [90]:
S_new = local_search.local_improve(S_first, G, sp, required_edges, K, threshold=1)
print(routes_cost(G, sp, S_new.routes))
for route in S_new.routes:
    for routestep in route:
        print(routestep)
    print("***")

3890346.0000000014
113 --> 110. (0) Salt value: 20000. Prev: None. Next: (110, 112, 2). Route end: False
110 --> 112. (2) Salt value: 19987.1938543755. Prev: (113, 110, 0). Next: (112, 114, 1). Route end: False
112 --> 114. (1) Salt value: 19957.96285376525. Prev: (110, 112, 2). Next: (114, 124, 2). Route end: False
114 --> 124. (2) Salt value: 19936.887968901. Prev: (112, 114, 1). Next: (124, 125, 2). Route end: False
124 --> 125. (2) Salt value: 19915.413542483748. Prev: (114, 124, 2). Next: (125, 111, 0). Route end: False
125 --> 111. (0) Salt value: 19908.58312176625. Prev: (124, 125, 2). Next: (111, 113, 1). Route end: False
111 --> 113. (1) Salt value: 19888.9712549215. Prev: (125, 111, 0). Next: (113, 110, 1). Route end: True
***
113 --> 110. (1) Salt value: 20000. Prev: (111, 113, 1). Next: (111, 113, 0). Route end: False
111 --> 113. (0) Salt value: 19985.64834935575. Prev: (113, 110, 1). Next: (110, 111, 0). Route end: False
110 --> 111. (0) Salt value: 20000. Prev: (111, 113

In [91]:
for route in S_new.routes:
    for routestep in route:
        print(routestep)
    print("***")

113 --> 110. (0) Salt value: 20000. Prev: None. Next: (110, 112, 2). Route end: False
110 --> 112. (2) Salt value: 19987.1938543755. Prev: (113, 110, 0). Next: (112, 114, 1). Route end: False
112 --> 114. (1) Salt value: 19957.96285376525. Prev: (110, 112, 2). Next: (114, 124, 2). Route end: False
114 --> 124. (2) Salt value: 19936.887968901. Prev: (112, 114, 1). Next: (124, 125, 2). Route end: False
124 --> 125. (2) Salt value: 19915.413542483748. Prev: (114, 124, 2). Next: (125, 111, 0). Route end: False
125 --> 111. (0) Salt value: 19908.58312176625. Prev: (124, 125, 2). Next: (111, 113, 1). Route end: False
111 --> 113. (1) Salt value: 19888.9712549215. Prev: (125, 111, 0). Next: (113, 110, 1). Route end: True
***
113 --> 110. (1) Salt value: 20000. Prev: (111, 113, 1). Next: (111, 113, 0). Route end: False
111 --> 113. (0) Salt value: 19985.64834935575. Prev: (113, 110, 1). Next: (110, 111, 0). Route end: False
110 --> 111. (0) Salt value: 20000. Prev: (111, 113, 0). Next: (111, 1

In [92]:
s1, s1req = construction.route_generation(G, sp)
S1 = Solution(s1req, dict(), routes_cost(G, sp, s1req), 0)
S1 = local_search.local_improve(S1, G, sp, required_edges, K, threshold=1)

s2, s2req = construction.route_generation(G, sp)
S2 = Solution(s2req, dict(), routes_cost(G, sp, s2req), 0)
S2 = local_search.local_improve(S2, G, sp, required_edges, K, threshold=1)

Problem with crossover: changing hte lenght of routes whcih shoiuldn't happen

In [100]:
required_edges = set(edge[:3] for edge in G.edges(data=True, keys=True) if edge[3]['priority'] != 0)
print(len(required_edges))

654


Why when removing duplicates does the route get longer?

In [131]:
count1, count2 = 0, 0

for route in S1.routes:
    for routestep in route:
        count1 += 1
for route in S2.routes:
    for routestep in route:
        count2 += 1


print(count1, count2)

654 654


In [139]:
S0 = apply_crossover(G, sp, S1.routes, S2.routes)
# idea for crossover: don't crossover a whole subsection of routes, but rather a fixed chunk (say 20-30 routesteps) of a route. This would significantly improve computation speed

AFter combining, route lenght is  586
Added route:  [113 --> 109. (0) Salt value: 20000. Prev: (108, 109, 0). Next: (113, 110, 1). Route end: True]
current step 109 --> 113. (1) Salt value: 19956.0706237275. Prev: (113, 109, 1). Next: (113, 110, 0). Route end: True
current step 113 --> 109. (1) Salt value: 20000. Prev: None. Next: (109, 113, 1). Route end: False
current step 111 --> 113. (2) Salt value: 19888.9712549215. Prev: (125, 111, 0). Next: (113, 109, 0). Route end: True
current step 125 --> 111. (0) Salt value: 19908.58312176625. Prev: (124, 125, 0). Next: (111, 113, 2). Route end: False
current step 124 --> 125. (0) Salt value: 19915.413542483748. Prev: (114, 124, 0). Next: (125, 111, 0). Route end: False
current step 114 --> 124. (0) Salt value: 19936.887968901. Prev: (112, 114, 0). Next: (124, 125, 0). Route end: False
current step 112 --> 114. (0) Salt value: 19957.96285376525. Prev: (113, 110, 0). Next: (114, 124, 0). Route end: False
current step 113 --> 110. (0) Salt val

KeyboardInterrupt: 

In [98]:
count0, count1, count2 = 0, 0, 0
for route in S0:
    for routestep in route:
        count0 += 1
for route in S1.routes:
    for routestep in route:
        count1 += 1
for route in S2.routes:
    for routestep in route:
        count2 += 1


print(count0, count1, count2)

730 654 654


In [95]:
# 4. Route Improvement Algorithms
sol = run_genetic(G, sp)

for route in sol.routes:
    for edge in route:
        print(edge)
    print("***")

initial generation 0
initial generation 1
initial generation 2
initial generation 3
initial generation 4
initial generation 5
initial generation 6
initial generation 7
initial generation 8
initial generation 9
Iteration 0
Iteration 1
Iteration 2
Iteration 3
Iteration 4
Iteration 5
Iteration 6
Iteration 7
Iteration 8
Iteration 9
Iteration 10
Iteration 11
Iteration 12
Iteration 13
Iteration 14


RecursionError: maximum recursion depth exceeded

In [ ]:

# 5. Plot final routes
G_graph = plotting.add_order_attribute(G, sol.routes)
plotting.draw_labeled_multigraph(G_graph, 'order', size=(75,75), plotDepot=True)

print("DONE")
print("Routes cost", sol.cost)

NameError: name 'sol' is not defined

## Plot the routes using Folium

In [ ]:
def full_routes(sp: ShortestPaths, routes: list[list[RouteStep]]):
    full_route = list()
    for i in range(len(routes)):
        for j in range(len(routes[i])):
            step = routes[i][j]
            next_step = routes[i][j+1] if j+1 < len(routes[i]) else routes[i+1][0] if i+1 < len(routes) else None
            if next_step is not None:
                if step.node2 == next_step.node1:
                    full_route.append(step.get_edge())
                else:
                    path = sp.get_shortest_path(step.get_edge(), next_step.get_edge())
                    full_route.extend(path)
                    full_route.pop()
            else:
                full_route.append(step.get_edge())
    return full_route

In [ ]:
full_route = full_routes(sp, S1.routes)

[(113, 109, 0),
 (109, 113, 0),
 (113, 113, 0),
 (113, 109, 1),
 (109, 113, 1),
 (113, 110, 0),
 (110, 112, 0),
 (112, 114, 0),
 (114, 124, 0),
 (124, 125, 2),
 (125, 111, 2),
 (111, 110, 0),
 (110, 112, 1),
 (112, 114, 0),
 (114, 124, 0),
 (124, 125, 0),
 (125, 111, 0),
 (111, 110, 1),
 (110, 112, 0),
 (112, 114, 0),
 (114, 124, 1),
 (124, 125, 1),
 (125, 111, 1),
 (111, 113, 2),
 (113, 113, 0),
 (113, 109, 0),
 (109, 108, 1),
 (108, 88, 0),
 (88, 87, 0),
 (87, 147, 0),
 (147, 63, 0),
 (63, 59, 0),
 (59, 56, 1),
 (56, 59, 0),
 (59, 56, 0),
 (56, 59, 0),
 (59, 57, 2),
 (57, 55, 0),
 (55, 56, 0),
 (56, 59, 0),
 (59, 64, 0),
 (64, 59, 1),
 (59, 64, 0),
 (64, 59, 0),
 (59, 64, 1),
 (64, 59, 0),
 (59, 57, 0),
 (57, 61, 0),
 (61, 149, 0),
 (149, 128, 0),
 (128, 118, 0),
 (118, 119, 0),
 (119, 45, 0),
 (45, 46, 2),
 (46, 47, 0),
 (47, 61, 0),
 (61, 149, 0),
 (149, 127, 0),
 (127, 50, 0),
 (50, 22, 0),
 (22, 50, 2),
 (50, 22, 0),
 (22, 9, 0),
 (9, 22, 1),
 (22, 50, 1),
 (50, 69, 2),
 (69, 68,

In [ ]:
new_m = folium.Map(location=[43.1, -89.5], zoom_start=12)
count = 0
for i, edge in enumerate(full_route):
    edge_data = G.get_edge_data(edge[0], edge[1], edge[2])
        
    if edge_data is not None:
            
        if i < len(full_route)-1:
            edge_data_next = G.get_edge_data(full_route[i+1][0], full_route[i+1][1], full_route[i+1][2])
            if edge_data_next is not None and "name" in edge_data_next and "name" in edge_data:
                if edge_data_next["name"] == edge_data["name"]:
                    continue
        lstring = edge_data['geometry']
        # swap long lat to lat long
        lstring = lstring.__class__([(y, x) for x, y in lstring.coords])
        midpoint = len(list(lstring.coords))//2
        icon_number = folium.plugins.BeautifyIcon(
            border_color="#00ABDC",
            border_width=1,
            text_color="#00ABDC",
            number=count,
            inner_icon_style="margin-top:2;",
        )
        folium.PolyLine(locations=lstring.coords, color='red', weight=1, tooltip=edge_data).add_to(new_m)
        folium.Marker(location=lstring.coords[midpoint], popup=f"Edge {count}", icon=icon_number).add_to(new_m)
        count += 1
new_m